In [ ]:
!pip install tweepy
!pip install jsonpickle

In [1]:
import tweepy
import jsonpickle
import time
import pandas as pd
import json
import csv

# Create convert json to csv

In [2]:
def createCSV_fromJson(csv_fname, txt_fname):
    f = open(csv_fname,'a',encoding='utf8')
    csvWriter = csv.writer(f)
    headers=['full_text','retweet_count','user_followers_count','favorite_count','place','coordinates','geo','created_at','id_str']
    #headers=['full_text']
    csvWriter.writerow(headers)

    for inputFile in [txt_fname]:#all the text-file names you want to convert to Csv in the sae folder as this code
        tweets = []
        for line in open(inputFile, 'r'):
            tweets.append(json.loads(line))

        
        count_lines=0
        for tweet in tweets:
            try:
                csvWriter.writerow([tweet['full_text'],tweet['retweet_count'],tweet['user']['followers_count'],tweet['favorite_count'],tweet['place'],tweet['coordinates'],tweet['geo'],tweet['created_at'],str(tweet['id_str'])])
                #csvWriter.writerow(tweet['full_text'])
                count_lines+=1
            except Exception as e:
                print(e)
        print(count_lines)

# Connect to Twitter using Tweepy api

In [3]:
# Variables that contains the credentials to access Twitter API
ACCESS_TOKEN = '1683653820-p2Ehkyl2OQUmaY7Xf7H9pc4ErNvyvovBVwxy9GC'
ACCESS_SECRET = 'TbtPT96BPIc31FK21b1iX9hcLfg4XOqiRZWrq5gAERoPc'

#CONSUMER_KEY / CONSUMER_SECRET
API_KEY = 'kUHB8y0fHK5WiGapp4CffpP2g'
API_SECRET ='Gd614dFtCjGWwgN9M4t6jVT83q5kntkyDFDRmpZE8D7JfGBLI7'

# Setup access to API
def connect_to_twitter_OAuth():
    auth = tweepy.OAuthHandler(API_KEY, API_SECRET)
    auth.set_access_token(ACCESS_TOKEN, ACCESS_SECRET)

    api = tweepy.API(auth)
    return api


In [4]:
# Create API object
api = connect_to_twitter_OAuth()
status = "Testing!"
#api.update_status(status=status)

# tweets from my stream

public_tweets = api.home_timeline()
for tweet in public_tweets:
    print(tweet.text)

# CreateJsonFile_ofTweets

In [6]:
def CreateJsonFile_ofTweets(fname, hashtag, max_tweets=1000000):
    #auth = tweepy.AppAuthHandler(API_KEY,API_SECRET)
    #api = tweepy.API(auth,wait_on_rate_limit=True,wait_on_rate_limit_notify=True)
    
    api = connect_to_twitter_OAuth()
    #wait_on_rate_limit – Whether or not to automatically wait for rate limits to replenish
    #wait_on_rate_limit_notify – Whether or not to print a notification when Tweepy is waiting for rate limits to replenish
    # the sleep mode is automatically enabled with above 2 args

    tweetsPerQuery = 100#this is the maximum provided by API
    #max_tweets just for the sake of While loop

    # No sinceId and max_id ..Get whathever you have exhaustively
    since_id = None
    max_id = -1
    tweet_count = 0
    print("Downloading the tweeets..takes some time..")

    search_query=hashtag 
    x=0
    with open(fname,'w') as f:
        print("Downloading hashtag" + search_query)
        while(tweet_count<max_tweets):
            try:
                if(max_id<=0):
                    if(not since_id):
                        new_tweets = api.search(q=search_query,count=tweetsPerQuery,lang="hi",
                                                tweet_mode='extended', include_rts=False)
                    else:
                        new_tweets = api.search(q=search_query,count=tweetsPerQuery,lang="hi",
                                                tweet_mode='extended',since_id=since_id, include_rts=False)
                else:
                    if(not since_id):
                        new_tweets = api.search(q=search_query,count=tweetsPerQuery,lang="hi",
                                                tweet_mode='extended',max_id=str(max_id-1), include_rts=False)
                    else:
                        new_tweets = api.search(q=search_query,count=tweetsPerQuery,lang="hi",tweet_mode='extended',
                                                max_id=str(max_id-1),since_id=since_id, include_rts=False)
                
                # Tweets Exhausted
                if(not new_tweets):
                    print("No more tweets found!!")
                    break
                    
                # write all the new_tweets to a json file
                for tweet in new_tweets:
                    f.write(jsonpickle.encode(tweet._json,unpicklable=False)+'\n')
                    tweet_count+=len(new_tweets)
                    #print("Successfully downloaded {0} tweets".format(tweet_count))
                    max_id=new_tweets[-1].id
                    
            # in case of any error
            except tweepy.TweepError as e:
                    print("Some error!!:"+str(e))
                    break
    return tweet_count

# tweets from a specific user

In [55]:
tweets = api.user_timeline(account, count=20000, lang="hi", tweet_mode="extended")

In [67]:
df

account                                               Text
0    Shanu44339200  RT @KapilMishra_IND: मुसलमानों को मारा, दलितों...
1    Shanu44339200  भंसाली ने दलाली खाकर सुबह से ही मीडिया फ़िल्म ...
2    Shanu44339200  काफी गहरे सदमे में हैं\nबाहर निकल कर एक जोर से...
3    Shanu44339200  जलती रही जोहर में नारियां\n भेड़िये फ़िरभी मौन...
4    Shanu44339200  ये अपने वाले #विश्व_विख्यात इटालियन ब्रांड\nके...
..             ...                                                ...
186  Shanu44339200  पूरे विधि विधान से कांग्रेस को\n\nराहु(ल) लग ग...
187  Shanu44339200  RT @RishiMishra_: सुबह की शुरुवात अच्छी खबर के...
188  Shanu44339200  दलित को अगर छींक भी आ जाए तो #मायावती रुमाल ले...
189  Shanu44339200  RT @republic: कर्नाटक में परेश की मौत के बाद, ...
190  Shanu44339200  RT @BJP4India: LIVE: PM Shri @narendramodi vis...

[191 rows x 2 columns]

account                                               Text
0    Shanu44339200  RT @KapilMishra_IND: मुसलमानों को मारा, दलितों...
1    Shanu44339200  भंसाली ने दलाली खाकर सुबह से ही मीडिया फ़िल्म ...
2    Shanu44339200  काफी गहरे सदमे में हैं\nबाहर निकल कर एक जोर से...
3    Shanu44339200  जलती रही जोहर में नारियां\n भेड़िये फ़िरभी मौन...
4    Shanu44339200  ये अपने वाले #विश्व_विख्यात इटालियन ब्रांड\nके...
..             ...                                                ...
386  sandeep353055  @KapilMishra_IND @richaanirudh https://t.co/5X...
387  sandeep353055                       @Shehzad_Ind Tag to karo sir
388  sandeep353055  RT @DrKumarVishwas: लाखों Cr की चुनावी-रेवड़िय...
389  sandeep353055  RT @swetasamadhiya: सुनो तुम और तुम्हारी सहेली...
390  sandeep353055  RT @TajinderBagga: Serving food is better than...

[391 rows x 2 columns]

191
191
Saving file sandeep353055.csv


In [7]:
accounts = ['acs_rkpandey','Bittu_Tufani','Gulmoha99443364','maliksarah5gma1','mjaved819',
'Rajeshkm_RJS','pallavinaharre1','raviag07','samratkikavitae','Sourav1717',
'Sujitkumar_mau','theBookwalla','gareeb_bhartiya','AkshayM90903668','vptvns',
'Vyang_Kumar','HindiSatire','Shanu44339200','SwetaSinghAT','VinodRajotiya82',
'Real_Netan','gautam007','sandeep353055','Republic_Bharat','VickyAarya007',
'KapilMishra_IND','VyangyaVahini','DChaurasia2312','WiskyWala','yatisharma111',
'ManojTiwariMP','Arnab5222','PbSwain_IND','chitraaum','RealPushpendra',
'RajatSharmaLive','RubikaLiyaquat','TheAbhishek_IND','Real_Sweta','SushantBSinha',
'VickyAarya007','badri_dk','Abhasin89009555','BhartiyRudr','Jainritesh_rj',
'PbSwain_IND','TeriJogan','ridhi_bose','DeshbhaktRosha1','ShrishtySharma_']

dfs=[]
for account in accounts:
    tweets = api.user_timeline(account, count=20000, lang="hi", tweet_mode="extended")
    tweets = [[account,tweet.full_text] for tweet in tweets]
    #tweets = (tweet for tweet in tweets)
    df = pd.DataFrame( tweets , columns=['account',"Text"])
    dfs.append(df)

for i in range(len(dfs)):
    print (len(dfs[i]))
    if i==0:
        df=dfs[0]
        i=1
    else:
        df=pd.concat( [df, dfs[i] ], ignore_index=True)
        i+=1
    
df.to_csv(account+".csv")
print ("Saving file "+account+".csv")


200
200
200
200
200
200
200
200
200
200
Saving file ShrishtySharma_.csv


In [9]:
tweet_count

10000

# tweets from a specific hashtag

max_tweets 100000
0
0 ===== [Status(_api=<tweepy.api.API object at 0x0000017ADEF69208>, _json={'created_at': 'Thu Jun 25 17:29:48 +0000 2020', 'id': 1276205968607473664, 'id_str': '1276205968607473664', 'full_text': 'RT @sumanthraman: Tamil Nadu becomes the first State in India to test 1 million samples for #covid . As of today 1008974 samples tested.', 'truncated': False, 'display_text_range': [0, 136], 'entities': {'hashtags': [{'text': 'covid', 'indices': [92, 98]}], 'symbols': [], 'user_mentions': [{'screen_name': 'sumanthraman', 'name': 'Sumanth Raman', 'id': 54436268, 'id_str': '54436268', 'indices': [3, 16]}], 'urls': []}, 'metadata': {'iso_language_code': 'en', 'result_type': 'recent'}, 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1245608764109012992, '

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



70000
70000 ===== [Status(_api=<tweepy.api.API object at 0x0000017ADEF69208>, _json={'created_at': 'Thu Jun 25 17:02:24 +0000 2020', 'id': 1276199075868823554, 'id_str': '1276199075868823554', 'full_text': "Just lost two different family members today to #COVID.\n\nWasn't close to them, but my mom was, and she's heartbroken.\n\nWear your fucking masks.", 'truncated': False, 'display_text_range': [0, 143], 'entities': {'hashtags': [{'text': 'COVID', 'indices': [48, 54]}], 'symbols': [], 'user_mentions': [], 'urls': []}, 'metadata': {'iso_language_code': 'en', 'result_type': 'recent'}, 'source': '<a href="https://mobile.twitter.com" rel="nofollow">Twitter Web App</a>', 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 1048762102238859266, 'id_str': '1048762102238859266', 'name': 'Paul Carpenter', 'screen_name': 'PwcCarpenter', 'location': 'Gaithersburg, MD', 'desc

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



1000
A total of 100000 tweets are downloaded and saved to COVID.txt
Total time taken is  19.467524766921997 seconds.
_COVID.csv file created
=====================>


In [7]:

hashtags= ["कटाक्ष", "#व्यंग", "व्यंग्य","मोदी_फिरकी_ले_रहा_है"]
#hashtags= ["मोदी_फिरकी_ले_रहा_है"]

for hashtag in hashtags:
    st = time.time()
    fname= hashtag+".txt"
    tweet_count = CreateJsonFile_ofTweets(fname, "#"+hashtag, 1000)
    createCSV_fromJson(hashtag+'.csv', hashtag+'.txt')
    end = time.time()
    print("A total of {0} tweets are downloaded and saved to {1}".format(tweet_count,fname))
    print("Total time taken is ",end-st,"seconds.")
    #df = pd.read_csv(hashtag+'.csv',  usecols=['created_at','full_text'], encoding = 'utf8')
    df = pd.read_csv(hashtag+'.csv',  usecols=['full_text'], encoding = 'utf8')
    
    df= df.rename(columns={'created_at':'Time','full_text':'Text'})
    df=df[ ['Time','Text'] ]
    df.to_csv("_"+hashtag+'.csv')
    print("_"+hashtag+'.csv'+ " file created")
    print ("=====================>")

100
A total of 10000 tweets are downloaded and saved to कटाक्ष.txt
Total time taken is  3.8153414726257324 seconds.
_कटाक्ष.csv file created
=====================>
100
A total of 10000 tweets are downloaded and saved to #व्यंग.txt
Total time taken is  3.1733458042144775 seconds.
_#व्यंग.csv file created
=====================>
54
A total of 2916 tweets are downloaded and saved to व्यंग्य.txt
Total time taken is  2.9097909927368164 seconds.
_व्यंग्य.csv file created
=====================>
No more tweets found!!
0
A total of 0 tweets are downloaded and saved to मोदी_फिरकी_ले_रहा_है.txt
Total time taken is  0.6580584049224854 seconds.
_मोदी_फिरकी_ले_रहा_है.csv file created
=====================>


In [161]:
pd.read_csv("_"+hashtags[0]+'.csv')

Unnamed: 0                            Time  \
0              0  Fri Jun 12 07:38:25 +0000 2020   
1              1  Fri Jun 12 07:15:19 +0000 2020   
2              2  Fri Jun 12 06:34:50 +0000 2020   
3              3  Thu Jun 11 23:57:02 +0000 2020   
4              4  Thu Jun 11 20:23:40 +0000 2020   
...          ...                             ...   
1408        1408  Tue Jun 09 07:51:43 +0000 2020   
1409        1409  Tue Jun 09 07:14:59 +0000 2020   
1410        1410  Tue Jun 09 04:33:54 +0000 2020   
1411        1411  Tue Jun 09 03:48:44 +0000 2020   
1412        1412  Tue Jun 09 03:32:15 +0000 2020   

                                                   Text  
0     मेरी साबुन बहुत जल्दी पिघल कर ख़त्म हो जा रही ...  
1     #कटाक्ष #व्यंग\r\n\r\n@INCIndia के दिग्गज नेता...  
2     अर्ज किया है :- \r\nअजब दलाली की गजब कहानी ......  
3     RT @meet_4735: अरे कौन कहेता है कि देश का Futu...  
4     70 वर्षों का हिसाब मांगने वाले लोग,  70 दिन का...  
...                                                 ...  
1408  RT @Dhaka_01: सारी PSU का निजीकरण कर दो अर्थव्...  
1409  RT @Raniiagrwal: कोरोना वैक्सीन के लिए बेजुबान...  
1410  फेसबुक ने भी कहा कि भाजपा नेता के भड़काऊ बयान ...  
1411  RT @SanjayKrShakya1: #कटाक्ष :-\r\nकोरोना कहर ...  
1412  RT @Dhaka_01: सारी PSU का निजीकरण कर दो अर्थव्...  

[1413 rows x 3 columns]

df = pd.read_csv(hashtags[0]+'.csv',  encoding = 'utf8')
df

# Remove all @ read text from Tweets

In [8]:
import pandas as pd
import re

In [77]:
len(df)

4096

In [9]:
df.Text

0       रागा- पता है मेरे जन्मदिन पे\nकौन पैदा हुआ था ...
1       जिस तरह राम रहीम के 36 अश्रम\nसील है उसी तरह म...
2       @mechitraaa @Abhasin89009555 ye to kuchh nhi h...
3       सुशांत सिंह राजपूत\nआत्महत्या मामले की सुप्रीम...
4       RT @Abhasin89009555: इन तस्वीरों को देखकर समझि...
                              ...                        
1995    RT @RajTiwa56444261: मित्रो आज हमारे विवाह के ...
1996    RT @its_mahii01: मै और मेरी तन्हाई अक्सर\n।\n।...
1997    RT @universe__guru: देश बचा लो साहब ,\nमोहब्बत...
1998    RT @Chatterj1Asking: लगता है 1962 का \nहिसाब ब...
1999    RT @shuklaji250: सुप्रभात, हर हर महादेव..!!🚩🙏🏻...
Name: Text, Length: 2000, dtype: object

In [78]:
account

'ManojTiwariMP'

In [10]:
df = pd.read_csv(account+".csv", index_col=None)

In [11]:
df

Unnamed: 0          account  \
0              0    VickyAarya007   
1              1    VickyAarya007   
2              2    VickyAarya007   
3              3    VickyAarya007   
4              4    VickyAarya007   
...          ...              ...   
1995        1995  ShrishtySharma_   
1996        1996  ShrishtySharma_   
1997        1997  ShrishtySharma_   
1998        1998  ShrishtySharma_   
1999        1999  ShrishtySharma_   

                                                   Text  
0     रागा- पता है मेरे जन्मदिन पे\nकौन पैदा हुआ था ...  
1     जिस तरह राम रहीम के 36 अश्रम\nसील है उसी तरह म...  
2     @mechitraaa @Abhasin89009555 ye to kuchh nhi h...  
3     सुशांत सिंह राजपूत\nआत्महत्या मामले की सुप्रीम...  
4     RT @Abhasin89009555: इन तस्वीरों को देखकर समझि...  
...                                                 ...  
1995  RT @RajTiwa56444261: मित्रो आज हमारे विवाह के ...  
1996  RT @its_mahii01: मै और मेरी तन्हाई अक्सर\n।\n।...  
1997  RT @universe__guru: देश बचा लो साहब ,\nमोहब्बत...  
1998  RT @Chatterj1Asking: लगता है 1962 का \nहिसाब ब...  
1999  RT @shuklaji250: सुप्रभात, हर हर महादेव..!!🚩🙏🏻...  

[2000 rows x 3 columns]

In [12]:
def getclean_text(x):
    text_list= x.split(" ")
    clean_text = []
    #don't include account
    pattern = "^[^@]"
    for token in text_list:
        if re.search(pattern, token):
            clean_text.append(token)
    
    #don't include http links
    clean_text1 = []
    pattern = "^[^http]*[^https]"
    for token in clean_text:
        if re.search(pattern, token):
            clean_text1.append(token)
    
    #print (clean_text1)
    clean_text1=" ".join(clean_text1)
    
    clean_text1= clean_text1.replace("\n"," ")
    
    return clean_text1

df1 = df[ ['account','Text'] ]
df1= pd.DataFrame(df1['Text'].apply(lambda x: getclean_text(x)) )

In [13]:
df1['account']=df.account

In [14]:
df1[ ['account','Text'] ].to_csv("_"+accounts[0]+".csv", index=False )
df1

Text          account
0     रागा- पता है मेरे जन्मदिन पे कौन पैदा हुआ था ?...    VickyAarya007
1     जिस तरह राम रहीम के 36 अश्रम सील है उसी तरह मौ...    VickyAarya007
2     ye kuchh nhi me Jane ke liye isse aage bhi bah...    VickyAarya007
3     सुशांत सिंह राजपूत आत्महत्या मामले की सुप्रीम ...    VickyAarya007
4     RT इन तस्वीरों को देखकर समझिए क्यों जरूरत पड़ी...    VickyAarya007
...                                                 ...              ...
1995  RT मित्रो आज हमारे विवाह के 18 वर्ष पूरे हुए.....  ShrishtySharma_
1996  RT मै और मेरी तन्हाई अक्सर । । । ।  चाइना वालो...  ShrishtySharma_
1997  RT देश बचा लो साहब , मोहब्बत तो कभी मिलने से र...  ShrishtySharma_
1998  RT लगता है 1962 का  हिसाब बराबर करना भी मोदीजी...  ShrishtySharma_
1999                   RT सुप्रभात, हर हर महादेव..!!🚩🙏🏻  ShrishtySharma_

[2000 rows x 2 columns]

In [7]:
import time 
from datetime import datetime
import numpy as np
# Fetch tweet ids from a timeline 
# Use these block if this is there is no saved tweets from 
# this account or you dont plan to use since_id functionality 
import time 
from datetime import datetime

counter = 0
timeline_ids = list()
start_time = datetime.now()

user_id='Shanu44339200'

try:
    for status in tweepy.Cursor(api.user_timeline, user_id=user_id).items():
        # process status here
        timeline_ids.append(status.id)
        end_time = datetime.now()
        if np.ceil((end_time - start_time).seconds / 60) >= 12:
            print("Worked for 12 minutes, waiting for 15 minutes now")
            print(datetime.now())
            time.sleep(60 * 15)
            start_time = datetime.now()
            end_time = datetime.now()

        counter += 1
except tweepy.RateLimitError as e:
    print("Rate limit error exceed waiting for 15 secs")
    print(datetime.now())
    print("You may want to save the timeline ids over there, to not to lose them during execution")
    time.sleep(60 * 15)
    start_time = datetime.now()
    end_time = datetime.now()

print("You may want to save the timeline ids over there, to not to lose them during execution")

You may want to save the timeline ids over there, to not to lose them during execution


In [12]:
import time 
from datetime import datetime

# Get the max_id that already  resides in db
max_id_in_town = 1000 #some_max_id
counter = 0
timeline_ids = list()
start_time = datetime.now()
try:
    for status in tweepy.Cursor(api.user_timeline, user_id=user_id, since_id=max_id_in_town).items():
        # process status here
        timeline_ids.append(status.id)
        print (status.created_at, status.text)
        end_time = datetime.now()
        if np.ceil((end_time - start_time).seconds / 60) >= 12:
            print("Worked for 12 mins, waiting for 15 mins now")
            print(datetime.now())
            print("You may want to save the timeline ids over there, to not to lose them during execution")
            time.sleep(60 * 15)
            start_time = datetime.now()
            end_time = datetime.now()

        counter += 1
except tweepy.RateLimitError as e:
    print("Rate limit error exceed waiting for 15 secs")
    print(datetime.now())
    print("You may want to save the timeline ids over there, to not to lose them during execution")
    time.sleep(60 * 15)
    start_time = datetime.now()
    end_time = datetime.now()
print("You may want to save the timeline ids over there, to not to lose them during execution")

2020-06-12 07:52:45 Testing!
2020-05-23 07:41:16 Testing!
2020-05-22 13:26:20 Testing!
2019-09-07 18:09:31 RT @PMBhutan: We are proud of India and its scientists today. Chandrayaan-2 saw some challenges last minute but the courage and hard work y…
2019-09-07 18:09:23 https://t.co/zIUnVdwrXu

#nonviolence #foodchain #survival
2019-09-07 07:26:16 @anandmahindra A true nationalist, patriotic, ethical business professional. India will always remember the way you… https://t.co/RoL5t0aVVs
2019-09-07 07:25:55 @anandmahindra every time I read your tweets. You occupy more space in my my mind and heart. Along with business, you are leader of masses.
2019-09-07 07:20:45 RT @anandmahindra: The communication isn’t lost. Every single person in India can feel the heartbeat of #chandrayaan2 We can hear it whispe…
2019-09-07 07:20:01 RT @RajivMessage: Chidambaram says his "only worry is about the economy." Does he mean his family economy?
https://t.co/R636ZVqwv1
2019-09-05 14:41:02 Causing #superintell

You may want to save the timeline ids over there, to not to lose them during execution


In [11]:
timeline_ids

[1271349705583149057,
 1264099059633012741,
 1263823512625541121,
 1170398707608473600,
 1170398673403969536,
 1170236828110082048,
 1170236739010433024,
 1170235441884172289,
 1170235256579903490,
 1169621463436935169,
 1169290402060361728,
 1168490249137225729,
 1168170950602326016,
 1167132916456947712,
 1166681205753827328,
 1162620242670915584,
 1161700086482472960,
 1159383510592843778,
 1158716559646289921,
 1157200449428062209,
 1156859328340512769,
 1141967034147729408,
 1141965921109467136,
 1141963627643039744,
 1135236232412258305,
 1133655734556725249,
 1079754796335316992,
 955734036227481600,
 870325962898059264,
 870299406859415552,
 870276275168059392,
 870273720081944576,
 870227409093709825,
 870199249140682757,
 870104872695345154,
 869950366229594114,
 869935614031998976,
 869910470941126656,
 869861790963904513,
 869836864764686336,
 869742482694840320,
 869588040511082496,
 869499378649755649,
 869474463871578112,
 868758381351374848,
 868757887274889216,
 868412

In [ ]:
# Set looping params
start_time = datetime.now()
raw_tweets = list()

for id_ in timeline_ids:
    try:
        res = api.get_status(id=id_, tweet_mode="extended")
        raw_tweets.append({"accident_id": id_,
                           "created_at": res.created_at,
                           "text": res.full_text})
        end_time = datetime.now()
   
        if np.ceil((end_time - start_time).seconds / 60) >= 12:
            print("Worked for 12 mins, waiting for 15 mins now")
            print(datetime.now())
            print("Save tweets somewhere")
            time.sleep(60 * 15)
            start_time = datetime.now()
            end_time = datetime.now()
        del res

    except tweepy.RateLimitError as e:
        print("Rate limit error exceed waiting for 15 secs")
        print(datetime.now())
        print("Save tweets somewhere")

        time.sleep(60 * 15)
        start_time = datetime.now()
        end_time = datetime.now()
print("Save tweets somewhere")